In [1]:
model_name='multi-qa-distilbert-cos-v1'
from sentence_transformers import SentenceTransformer
embedding_model = SentenceTransformer(model_name)

/home/gary/.local/lib/python3.10/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange
2024-07-14 09:30:52.285927: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-07-14 09:30:53.005889: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
user_question = "I just discovered the course. Can I still join it?"

In [3]:
embedding_model.encode(user_question)

array([ 7.82226250e-02, -4.01311629e-02,  3.86136249e-02, -1.78954346e-04,
        8.92346650e-02, -5.04591465e-02, -1.05026867e-02,  3.71055827e-02,
       -4.18714099e-02,  3.48084681e-02, -1.20702004e-02, -2.36942545e-02,
        3.87899801e-02,  1.60988104e-02,  3.50747257e-02,  3.04752099e-03,
        5.79672307e-02, -4.10627425e-02, -3.41552682e-02, -2.56396104e-02,
       -3.55264097e-02,  1.42908068e-02, -1.62800159e-02,  3.21446508e-02,
       -4.66897413e-02,  7.89185837e-02,  4.90160994e-02,  1.56761035e-02,
       -1.69109982e-02,  2.26482321e-02,  5.60206249e-02, -3.98361459e-02,
        6.77409619e-02, -1.20210275e-02,  1.12626038e-03, -1.94394458e-02,
       -2.65951175e-02,  1.06177870e-02,  1.69687495e-02,  1.13487933e-02,
       -2.97063179e-02,  5.25258668e-02, -1.41453594e-02,  4.61700037e-02,
        1.17066130e-02, -2.38053016e-02, -6.32558167e-02, -1.92042030e-02,
       -7.10596005e-03,  3.24167833e-02,  2.49617994e-02, -5.27500920e-03,
        2.01149546e-02, -

In [12]:
v = embedding_model.encode(user_question)

In [13]:
scores = X.dot(v)

In [14]:
scores.max()

0.6506573

In [15]:
import requests 

base_url = 'https://github.com/DataTalksClub/llm-zoomcamp/blob/main'
relative_url = '03-vector-search/eval/documents-with-ids.json'
docs_url = f'{base_url}/{relative_url}?raw=1'
docs_response = requests.get(docs_url)
documents = docs_response.json()

In [16]:
documents = [x for x in documents if x['course']=='machine-learning-zoomcamp']

In [17]:
len(documents)

375

In [18]:
embeddings = []

In [19]:
for doc in documents:
    # print(f"{doc['question']}")

    qa_text = f"{doc['question']} {doc['text']}"

    emb = embedding_model.encode(qa_text)
    embeddings.append(emb)


In [16]:
# embeddings

In [9]:
import numpy as np

In [10]:
X = np.array(embeddings)

In [11]:
X.shape

(375, 768)

In [26]:
import pandas as pd

base_url = 'https://github.com/DataTalksClub/llm-zoomcamp/blob/main'
relative_url = '03-vector-search/eval/ground-truth-data.csv'
ground_truth_url = f'{base_url}/{relative_url}?raw=1'

df_ground_truth = pd.read_csv(ground_truth_url)
df_ground_truth = df_ground_truth[df_ground_truth.course == 'machine-learning-zoomcamp']
ground_truth = df_ground_truth.to_dict(orient='records')


In [27]:
class VectorSearchEngine():
    def __init__(self, documents, embeddings):
        self.documents = documents
        self.embeddings = embeddings

    def search(self, v_query, num_results=10):
        scores = self.embeddings.dot(v_query)
        idx = np.argsort(-scores)[:num_results]
        return [self.documents[i] for i in idx]

search_engine = VectorSearchEngine(documents=documents, embeddings=X)
results = search_engine.search(v, num_results=5)


In [30]:
def calculate_hit_rate(search_engine, ground_truth, num_results=5):
    hits = 0
    for item in ground_truth:
        query = item['question']
        expected_document_id = item['document']
        query_embedding = embedding_model.encode(query)
        results = search_engine.search(query_embedding, num_results)
        retrieved_ids = [doc['id'] for doc in results]
        if expected_document_id in retrieved_ids:
            hits += 1
    return hits / len(ground_truth)

hit_rate = calculate_hit_rate(search_engine, ground_truth, num_results=5)
print(hit_rate)

0.9398907103825137


In [29]:
print(ground_truth[:5])

[{'question': 'Where can I sign up for the course?', 'course': 'machine-learning-zoomcamp', 'document': '0227b872'}, {'question': 'Can you provide a link to sign up?', 'course': 'machine-learning-zoomcamp', 'document': '0227b872'}, {'question': 'Is there an FAQ for this Machine Learning course?', 'course': 'machine-learning-zoomcamp', 'document': '0227b872'}, {'question': 'Does this course have a GitHub repository for the sign-up link?', 'course': 'machine-learning-zoomcamp', 'document': '0227b872'}, {'question': 'How can I structure my questions and answers for the course?', 'course': 'machine-learning-zoomcamp', 'document': '0227b872'}]


In [33]:
from elasticsearch import Elasticsearch
es_client = Elasticsearch('http://localhost:9200') 

es_client.info()

ObjectApiResponse({'name': '28aaa8f24107', 'cluster_name': 'docker-cluster', 'cluster_uuid': 'AGiapfl4RCq1JdYrVRw9Lg', 'version': {'number': '8.4.3', 'build_flavor': 'default', 'build_type': 'docker', 'build_hash': '42f05b9372a9a4a470db3b52817899b99a76ee73', 'build_date': '2022-10-04T07:17:24.662462378Z', 'build_snapshot': False, 'lucene_version': '9.3.0', 'minimum_wire_compatibility_version': '7.17.0', 'minimum_index_compatibility_version': '7.0.0'}, 'tagline': 'You Know, for Search'})

In [34]:
embeddings

[array([ 8.80590975e-02,  1.55936414e-02,  7.92557523e-02,  2.52757873e-02,
         7.55764544e-02, -3.90596576e-02, -4.13813144e-02,  2.52917018e-02,
         2.43241154e-02,  3.62588698e-03, -7.28290575e-03, -3.28750871e-02,
         6.12956472e-02, -5.71100302e-02,  1.16774915e-02, -1.79441571e-02,
         4.49205637e-02, -5.41606732e-02, -1.92254549e-03,  1.48329679e-02,
         7.91346282e-03, -3.43126804e-02,  1.21480739e-02,  1.27186067e-02,
        -1.60091538e-02,  7.12129334e-03,  1.58389118e-02, -3.27577436e-04,
         3.01294983e-03, -4.58917357e-02, -1.34771829e-03,  2.01150198e-02,
         2.33724006e-02, -4.28201351e-03, -3.09382826e-02,  1.94304902e-03,
        -1.88219231e-02,  5.35164634e-03,  1.29352892e-02, -3.23958993e-02,
         3.10556535e-02,  5.12984721e-03, -3.24451219e-04, -3.15542296e-02,
         1.93376988e-02, -6.38601556e-02, -3.05380933e-02, -6.27885535e-02,
        -1.74859986e-02,  3.52948830e-02, -2.98071075e-02,  7.45346099e-02,
        -2.0

In [36]:
index_settings = {
    "settings": {
        "number_of_shards": 1,
        "number_of_replicas": 0
    },
    "mappings": {
        "properties": {
            "text": {"type": "text"},
            "section": {"type": "text"},
            "question": {"type": "text"},
            "course": {"type": "keyword"},
            "text_vector": {"type": "dense_vector", "dims": 768, "index": True, "similarity": "cosine"}
        }
    }
}

# Create the index
index_name = "llm-zoomcamp-index"
if es_client.indices.exists(index=index_name):
    es_client.indices.delete(index=index_name)
es_client.indices.create(index=index_name, body=index_settings)

ObjectApiResponse({'acknowledged': True, 'shards_acknowledged': True, 'index': 'llm-zoomcamp-index'})

In [38]:
from tqdm import tqdm

# Index each document with its embedding
for doc, embedding in tqdm(zip(documents, embeddings), total=len(documents)):
    doc_body = {
        "text": doc['text'],
        "section": doc['section'],
        "question": doc['question'],
        "course": doc['course'],
        "text_vector": embedding.tolist()
    }
    es_client.index(index=index_name, body=doc_body)

100%|██████████| 375/375 [00:02<00:00, 161.25it/s]


In [40]:
from sentence_transformers import SentenceTransformer

# Use the same embedding model
embedding_model = SentenceTransformer('multi-qa-distilbert-cos-v1')

# Create the query embedding
user_question = "I just discovered the course. Can I still join it?"
query_embedding = embedding_model.encode(user_question)

# Perform the search
search_body = {
    "query": {
        "script_score": {
            "query": {
                "match_all": {}
            },
            "script": {
                "source": "cosineSimilarity(params.query_vector, 'text_vector') + 1.0",
                "params": {
                    "query_vector": query_embedding.tolist()
                }
            }
        }
    },
    "size": 1
}

# Execute the search
response = es_client.search(index=index_name, body=search_body)


In [41]:
highest_score_doc_id = response['hits']['hits'][0]['_id']
print(highest_score_doc_id)

un2_sZABrx7giLehlHuF


In [44]:
from sentence_transformers import SentenceTransformer
from elasticsearch import Elasticsearch
import numpy as np

# Initialize the embedding model and Elasticsearch client
embedding_model = SentenceTransformer('multi-qa-distilbert-cos-v1')
es = Elasticsearch("http://localhost:9200")

# Function to calculate hit rate
def calculate_hit_rate_elasticsearch(search_engine, ground_truth, num_results=5):
    hits = 0
    for item in ground_truth:
        query = item['question']
        expected_document_id = str(item['document'])  # Ensure it's a string
        query_embedding = embedding_model.encode(query)

        # Elasticsearch search query
        search_body = {
            "query": {
                "script_score": {
                    "query": {
                        "match_all": {}
                    },
                    "script": {
                        "source": "cosineSimilarity(params.query_vector, 'text_vector') + 1.0",
                        "params": {
                            "query_vector": query_embedding.tolist()
                        }
                    }
                }
            },
            "size": num_results
        }

        response = es.search(index='llm-zoomcamp-index', body=search_body)
        retrieved_ids = [hit['_id'] for hit in response['hits']['hits']]

        if expected_document_id in retrieved_ids:
            hits += 1
    return hits / len(ground_truth)

# Calculate the hit rate for Elasticsearch
hit_rate_elastic = calculate_hit_rate_elasticsearch(es, ground_truth, num_results=5)
print(f"Hit Rate with Elasticsearch: {hit_rate_elastic}")


Hit Rate with Elasticsearch: 0.0
